In [51]:
import json
import numpy as np
from pathlib import Path
from sklearn.model_selection import train_test_split
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.utils import to_categorical

from tensorflow.keras.models import Model
from tensorflow.keras.layers import (
    Input,
    Embedding,
    LSTM,
    Concatenate,
    Dense,
    TimeDistributed,
)
from tensorflow.keras.callbacks import EarlyStopping
from sklearn.metrics import classification_report
from collections import Counter

In [52]:
# Load raw data
with open("qg_dataset.json", encoding="utf-8") as f:
    raw_data = json.load(f)

# Validasi lengkap
required_keys = {"tokens", "ner", "srl", "question", "answer", "type"}
valid_data = []
invalid_data = []

for idx, item in enumerate(raw_data):
    error_messages = []

    if not isinstance(item, dict):
        error_messages.append("bukan dictionary")

    missing_keys = required_keys - item.keys()
    if missing_keys:
        error_messages.append(f"missing keys: {missing_keys}")

    if not error_messages:
        # Cek tipe data dan None
        if (not isinstance(item["tokens"], list) or
            not isinstance(item["ner"], list) or
            not isinstance(item["srl"], list) or
            not isinstance(item["question"], list) or
            not isinstance(item["answer"], list) or
            not isinstance(item["type"], str)):
            error_messages.append("field type tidak sesuai")
    
    if error_messages:
        print(f"\n Index {idx} | Masalah: {', '.join(error_messages)}")
        print(json.dumps(item, indent=2, ensure_ascii=False))
        invalid_data.append(item)
        continue

    valid_data.append(item)

# Statistik
print(f"\n Jumlah data valid: {len(valid_data)} / {len(raw_data)}")
print(f" Jumlah data tidak valid: {len(invalid_data)}")

# Proses data valid
tokens = [[t.lower().strip() for t in item["tokens"]] for item in valid_data]
ner_tags = [item["ner"] for item in valid_data]
srl_tags = [item["srl"] for item in valid_data]
questions = [[token.lower().strip() for token in item["question"]] for item in valid_data]
answers = [[token.lower().strip() for token in item["answer"]] for item in valid_data]
types = [item["type"] for item in valid_data]

type_counts = Counter(types)

print(type_counts)



 Jumlah data valid: 70 / 70
 Jumlah data tidak valid: 0
Counter({'tof': 30, 'isian': 30, 'opsi': 10})


In [53]:
# tokenize
token_tok = Tokenizer(lower=False, oov_token="UNK")
token_ner = Tokenizer(lower=False)
token_srl = Tokenizer(lower=False)
token_q = Tokenizer(lower=False)
token_a = Tokenizer(lower=False)
token_type = Tokenizer(lower=False)

token_tok.fit_on_texts(tokens)
token_ner.fit_on_texts(ner_tags)
token_srl.fit_on_texts(srl_tags)
token_q.fit_on_texts(questions)
token_a.fit_on_texts(answers)
token_type.fit_on_texts(types)


maxlen = 20

In [54]:

X_tok = pad_sequences(
    token_tok.texts_to_sequences(tokens), padding="post", maxlen=maxlen
)
X_ner = pad_sequences(
    token_ner.texts_to_sequences(ner_tags), padding="post", maxlen=maxlen
)
X_srl = pad_sequences(
    token_srl.texts_to_sequences(srl_tags), padding="post", maxlen=maxlen
)
y_q = pad_sequences(token_q.texts_to_sequences(questions), padding="post", maxlen=maxlen)
y_a = pad_sequences(token_a.texts_to_sequences(answers), padding="post", maxlen=maxlen)

print(set(types))

y_type = [seq[0] for seq in token_type.texts_to_sequences(types)]  # list of int
y_type = to_categorical(np.array(y_type) - 1, num_classes=len(token_type.word_index))



{'isian', 'tof', 'opsi'}


In [55]:
X_tok_train, X_tok_test, X_ner_train, X_ner_test, X_srl_train, X_srl_test, \
y_q_train, y_q_test, y_a_train, y_a_test, y_type_train, y_type_test = train_test_split(
    X_tok, X_ner, X_srl, y_q, y_a, y_type, test_size=0.2, random_state=42
)

X_train = [X_tok_train, X_ner_train, X_srl_train]
X_test = [X_tok_test, X_ner_test, X_srl_test]

In [56]:

inp_tok = Input(shape=(None,), name="tok_input")
inp_ner = Input(shape=(None,), name="ner_input")
inp_srl = Input(shape=(None,), name="srl_input")

emb_tok = Embedding(input_dim=len(token_tok.word_index) + 1, output_dim=128)(inp_tok)
emb_ner = Embedding(input_dim=len(token_ner.word_index) + 1, output_dim=16)(inp_ner)
emb_srl = Embedding(input_dim=len(token_srl.word_index) + 1, output_dim=16)(inp_srl)

# emb_tok = Embedding(input_dim=..., output_dim=..., mask_zero=True)(inp_tok)
# emb_ner = Embedding(input_dim=..., output_dim=..., mask_zero=True)(inp_ner)
# emb_srl = Embedding(input_dim=..., output_dim=..., mask_zero=True)(inp_srl)

merged = Concatenate()([emb_tok, emb_ner, emb_srl])

x = LSTM(256, return_sequences=True)(merged)

out_question = TimeDistributed(Dense(len(token_q.word_index) + 1, activation="softmax"), name="question_output")(x)
out_answer = TimeDistributed(Dense(len(token_a.word_index) + 1, activation="softmax"), name="answer_output")(x)
out_type = Dense(len(token_type.word_index), activation="softmax", name="type_output")(
    x[:, 0, :]
)  # gunakan step pertama

model = Model(
    inputs=[inp_tok, inp_ner, inp_srl], outputs=[out_question, out_answer, out_type]
)
model.compile(
    optimizer="adam",
    loss={
        "question_output": "sparse_categorical_crossentropy",
        "answer_output": "sparse_categorical_crossentropy",
        "type_output": "categorical_crossentropy",
    },
    metrics={
        "question_output": "accuracy",
        "answer_output": "accuracy",
        "type_output": "accuracy",
    },
)

model.summary()

# ----------------------------------------------------------------------------
# 5. TRAINING
# ----------------------------------------------------------------------------
model.fit(
    X_train,
    {
        "question_output": np.expand_dims(y_q_train, -1),
        "answer_output": np.expand_dims(y_a_train, -1),
        "type_output": y_type_train,
    },
    batch_size=64,
    epochs=30,
    validation_split=0.1,
    callbacks=[EarlyStopping(patience=3, restore_best_weights=True)],
)

import pickle


model.save("new_model_lstm_qg.keras")
with open("tokenizers.pkl", "wb") as f:
    pickle.dump({
        "token": token_tok,
        "ner": token_ner,
        "srl": token_srl,
        "question": token_q,
        "answer": token_a,
        "type": token_type
    }, f)



Model: "functional_5"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ tok_input           │ (None, None)      │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ ner_input           │ (None, None)      │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ srl_input           │ (None, None)      │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ embedding_15        │ (None, None, 128) │     41,600 │ tok_input[0][0]   │
│ (Embedding)         │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ embedding_16        │ (None, None, 16)  │        272 │ ner_input[0][0]   │
│ (Embedding)         │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ embedding_17        │ (None, None, 16)  │        272 │ srl_input[0][0]   │
│ (Embedding)         │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ concatenate_5       │ (None, None, 160) │          0 │ embedding_15[0][… │
│ (Concatenate)       │                   │            │ embedding_16[0][… │
│                     │                   │            │ embedding_17[0][… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ lstm_5 (LSTM)       │ (None, None, 256) │    427,008 │ concatenate_5[0]… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ get_item_5          │ (None, 256)       │          0 │ lstm_5[0][0]      │
│ (GetItem)           │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ question_output     │ (None, None, 272) │     69,904 │ lstm_5[0][0]      │
│ (TimeDistributed)   │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ answer_output       │ (None, None, 60)  │     15,420 │ lstm_5[0][0]      │
│ (TimeDistributed)   │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ type_output (Dense) │ (None, 3)         │        771 │ get_item_5[0][0]  │
└─────────────────────┴───────────────────┴────────────┴───────────────────┘

 Total params: 555,247 (2.12 MB)

 Trainable params: 555,247 (2.12 MB)

 Non-trainable params: 0 (0.00 B)

Epoch 1/30
1/1 ━━━━━━━━━━━━━━━━━━━━ 3s 3s/step - answer_output_accuracy: 0.0030 - answer_output_loss: 4.1163 - loss: 10.8193 - question_output_accuracy: 0.0030 - question_output_loss: 5.6031 - type_output_accuracy: 0.2000 - type_output_loss: 1.0999 - val_answer_output_accuracy: 0.8833 - val_answer_output_loss: 4.0123 - val_loss: 10.6706 - val_question_output_accuracy: 0.6000 - val_question_output_loss: 5.5595 - val_type_output_accuracy: 0.1667 - val_type_output_loss: 1.0987
Epoch 2/30
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 95ms/step - answer_output_accuracy: 0.8800 - answer_output_loss: 4.0174 - loss: 10.6778 - question_output_accuracy: 0.5640 - question_output_loss: 5.5631 - type_output_accuracy: 0.4200 - type_output_loss: 1.0973 - val_answer_output_accuracy: 0.9250 - val_answer_output_loss: 3.8939 - val_loss: 10.4860 - val_question_output_accuracy: 0.6250 - val_question_output_loss: 5.4945 - val_type_output_accuracy: 0.3333 - val_type_output_loss: 1.0976
Epoch 3/30
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 9

In [57]:

def token_level_accuracy(y_true, y_pred):
    correct = 0
    total = 0
    for true_seq, pred_seq in zip(y_true, y_pred):
        for t, p in zip(true_seq, pred_seq):
            if t != 0:  # ignore padding
                total += 1
                if t == p:
                    correct += 1
    return correct / total if total > 0 else 0


# Predict on test set
y_pred_q, y_pred_a, y_pred_type = model.predict(X_test)

# Decode predictions to class indices
y_pred_q = np.argmax(y_pred_q, axis=-1)
y_pred_a = np.argmax(y_pred_a, axis=-1)
y_pred_type = np.argmax(y_pred_type, axis=-1)
y_true_type = np.argmax(y_type_test, axis=-1)

# Calculate token-level accuracy
acc_q = token_level_accuracy(y_q_test, y_pred_q)
acc_a = token_level_accuracy(y_a_test, y_pred_a)

# Type classification report
report_type = classification_report(y_true_type, y_pred_type, zero_division=0)

# Print Results
print("\n=== Akurasi Detail ===")
print(f"Question Accuracy (Token-level): {acc_q:.4f}")
print(f"Answer Accuracy (Token-level)  : {acc_a:.4f}")
print(f"Type Accuracy (Class-level)   : {np.mean(y_true_type == y_pred_type):.2f}")

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 239ms/step

=== Akurasi Detail ===
Question Accuracy (Token-level): 0.0000
Answer Accuracy (Token-level)  : 0.0000
Type Accuracy (Class-level)   : 0.29


In [58]:
# import sacrebleu
# from sacrebleu.metrics import BLEU   # optional kalau mau smoothing/effective_order

# idx2tok = {v:k for k,v in word2idx.items()}
# PAD_ID   = word2idx["PAD"]
# SOS_ID   = word2idx.get("SOS", None)
# EOS_ID   = word2idx.get("EOS", None)

# def seq2str(seq):
#     """Konversi list index -> kalimat string, sambil buang token spesial."""
#     toks = [idx2tok[i] for i in seq
#             if i not in {PAD_ID, SOS_ID, EOS_ID}]
#     return " ".join(toks).strip().lower()

# bleu_metric = BLEU(effective_order=True)  # lebih stabil utk kalimat pendek

# def bleu_corpus(pred_seqs, true_seqs):
#     preds = [seq2str(p) for p in pred_seqs]
#     refs  = [[seq2str(t)] for t in true_seqs]  # list‑of‑list, satu ref/kalimat
#     return bleu_metric.corpus_score(preds, refs).score


In [59]:

# flat_true_a, flat_pred_a = flatten_valid(y_a_test, y_pred_a_class)
# print("\n=== Classification Report: ANSWER ===")
# print(classification_report(flat_true_a, flat_pred_a))


In [60]:

# print("\n=== Classification Report: TYPE ===")
# print(classification_report(y_true_type_class, y_pred_type_class))